<div class="alert alert-block alert-info"> <b>NOTE</b> Please select the kernel <code>Python [conda env: deepcell]</code> for this notebook. </div>

# 1. Data Preparation
Resave data as a set of tiff files in order to match Cell Tracking Challenge conventions which are expected by Baxter

In [8]:
import os
import sys

import numpy as np
from tifffile import imwrite

from deepcell.applications import NuclearSegmentation
from deepcell.datasets import DynamicNuclearNetTracking
from deepcell_tracking.isbi_utils import trk_to_isbi

sys.path.append('..')
import utils

In [9]:
data_dir = 'data'
raw_dir = os.path.join(data_dir, 'raw')
seg_gt_dir = os.path.join(raw_dir, 'Analysis/Segmentation_GT')
seg_dc_dir = os.path.join(raw_dir, 'Analysis/Segmentation_DeepCell')
gt_dir = os.path.join(data_dir, 'GT')

for d in [raw_dir, seg_gt_dir, seg_dc_dir, gt_dir]:
    if not os.path.exists(d):
        os.makedirs(d)

Load the test split of the tracking data

In [10]:
# Load test data
dnn = DynamicNuclearNetTracking(version='1.1')
X, y, lineages = dnn.load_data(split='test')
data = {
    'X': X,
    'y': y,
    'lineages': lineages
}

INFO:root:Checking for cached data
INFO:root:Checking DynamicNuclearNet-tracking-v1_1.zip against provided file_hash...
INFO:root:DynamicNuclearNet-tracking-v1_1.zip with hash 4090ccd3b76c27f001f798c8187c5f3e already available.
INFO:root:Extracting /Users/morganschwartz/.deepcell/datasets/DynamicNuclearNet-tracking-v1_1.zip
INFO:root:Successfully extracted /Users/morganschwartz/.deepcell/datasets/DynamicNuclearNet-tracking-v1_1.zip into /Users/morganschwartz/.deepcell/datasets


Load the DeepCell nuclear segmentation model to test the algorithm on predicted instead of ground truth segmentations

In [11]:
app_seg = NuclearSegmentation.from_version(version='1.1')

INFO:root:Checking for cached data
INFO:root:Checking NuclearSegmentation-8.tar.gz against provided file_hash...
INFO:root:NuclearSegmentation-8.tar.gz with hash 507be21f0e34e59adae689f58cc03ccb already available.
INFO:root:Extracting /Users/morganschwartz/.deepcell/models/NuclearSegmentation-8.tar.gz
INFO:root:Successfully extracted /Users/morganschwartz/.deepcell/models/NuclearSegmentation-8.tar.gz into /Users/morganschwartz/.deepcell/models


Convert each batch of the test split to the standard ISBI format which is compatible with most of the models that we will test.

In [12]:
for batch_no in range(len(data['lineages'])):
    # Build subdirectories for data
    raw_subdir = os.path.join(raw_dir, '{:03}'.format(batch_no + 1))
    gt_subdir = os.path.join(gt_dir, '{:03}'.format(batch_no + 1))
    seg_gt_subdir = os.path.join(seg_gt_dir, '{:03}'.format(batch_no + 1))
    seg_dc_subdir = os.path.join(seg_dc_dir, '{:03}'.format(batch_no + 1))

    # Create directories if needed
    for d in (raw_subdir, gt_subdir, seg_gt_subdir, seg_dc_subdir):
        if not os.path.exists(d):
            os.makedirs(d)

    # Pull out relevant data for this batch
    X = data['X'][batch_no]
    y = data['y'][batch_no]
    lineage = data['lineages'][batch_no]

    # Correct discontiguous tracks, which are not allowed by CTC
    y, lineage = utils.convert_to_contiguous(y, lineage)

    # Determine position of zero padding for removal
    slc = utils.find_zero_padding(X)
    X = X[slc]
    y = y[slc]

    # Determine which frames are zero padding
    frames = np.sum(y, axis=(1,2)) # True if image not blank
    good_frames = np.where(frames)[0]
    X = X[:len(good_frames)]
    y = y[:len(good_frames)]

    # Need to translate lineages and adjust images to match restrictive ISBI format
    # Prepare output txt
    text_file = os.path.join(gt_subdir, 'man_track.txt')
    df = trk_to_isbi(lineage)
    df.to_csv(text_file, sep=' ', header=False, index=False)

    # Save each frame of the movie as an individual tif
    channel = 0 # These images should only have one channel
    for i in range(X.shape[0]):
        name_raw = os.path.join(raw_subdir, 't{:03}.tif'.format(i))
        name_seg_gt = os.path.join(seg_gt_subdir, 't{:03}.tif'.format(i))
        name_seg_dc = os.path.join(seg_dc_subdir, 't{:03}.tif'.format(i))
        name_gt = os.path.join(gt_subdir, 't{:03}.tif'.format(i))

        # Generate deepcell prediction
        pred = app_seg.predict(X[i:i+1, ..., channel:channel+1])

        imwrite(name_raw, X[i, ..., channel])
        imwrite(name_seg_gt, y[i, ..., channel].astype('uint16'))
        imwrite(name_seg_dc, pred.astype('uint16'))
        imwrite(name_gt, y[i, ..., channel].astype('uint16'))

INFO:root:Converting image dtype to float
2024-07-05 11:40:12.830382: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.
2024-07-05 11:40:22.449576: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converting image dtype to float
INFO:root:Converti

# 2. Tracking

The steps for tracking will be performed in Matlab and the Baxter Algorithm GUI. You will need access to Matlab 2019b. The instructions below outline the general workflow for generating benchmarking results using the Baxter algorithm. However additional support for using the software is available in the user guide located in the KTH-SE folder (`KTH-SE/UserGuide/UserGuide.pdf`).

## Part 1 - Setup
1. Open the KTH-SE folder in Matlab
2. Open `BaxterAlgorithms.m` in the Matlab editor and then hit Run. This should open a GUI.
3. Within the GUI, select `Files > Open experiment > Browse...`. Navigate to the `data/raw` folder located within this Baxter folder.
4. Ensure that all files are selected in the list on the right hand side of the GUI.
## Part 2 - GT Segmentations
5. Select `Settings > Load Settings (Browse for files)`. Navigate to `Settings-SegmentationGT.csv` within the Baxter folder. In the following prompts, ensure that segmentations are applied to all images.
6. Select `Automated > Track`. In the pop-up window, change the `Save Version` to "GT" and press `Start`. 
7. Select `File > Export tracks to CTC format > RES tracks` and follow the prompts in order to export the tracking results to the standard CTC format. Make sure to select the "GT" version for export.
## Part 3 - DeepCell Segmentations
8. Select `Settings > Load Settings (Browse for files)`. Navigate to `Settings-SegmentationDeepCell.csv` within the Baxter folder. In the following prompts, ensure that segmentations are applied to all images.
6. Select `Automated > Track`. In the pop-up window, change the `Save Version` to "DeepCell" and press `Start`. 
7. Select `File > Export tracks to CTC format > RES tracks` and follow the prompts in order to export the tracking results to the standard CTC format. Make sure to select the "DeepCell" version for export.


# 3. Evaluation

In [13]:
import os
import re
import shutil
import subprocess

import pandas as pd

from deepcell_tracking.metrics import TrackingMetrics

In [14]:
data_dir = 'data'
gt_dir = os.path.join(data_dir, 'GT')
export_gt_dir = os.path.join(data_dir, 'raw/Analysis/CellDataGT/RES/')
export_dc_dir = os.path.join(data_dir, 'raw/Analysis/CellDataDeepCell/RES/')
ctc_gt = os.path.join(data_dir, 'SEG_GT')
ctc_dc = os.path.join(data_dir, 'SEG_PRED')

data_ids = os.listdir(gt_dir)

node_match_threshold = 0.6

ctc_software = '../CTC_Evaluation_Software'
operating_system = 'Mac' # or 'Mac' or 'Win'
num_digits = '3'

In order to utilize the CTC evaluation functions, the data must be reorganized to match CTC conventions.

In [15]:
# Copy the GT data over to appropriate folders
for target in [ctc_gt, ctc_dc]:
    for d in os.listdir(gt_dir):
        seg_dir = os.path.join(target, f'{d}_GT/SEG')
        tra_dir = os.path.join(target, f'{d}_GT/TRA')
        if not os.path.exists(seg_dir): os.makedirs(seg_dir)
        if not os.path.exists(tra_dir): os.makedirs(tra_dir)

        for f in os.listdir(os.path.join(gt_dir, d)):
            start_path = os.path.join(gt_dir, d, f)

            # Only copy the txt file with tracks to TRA dir
            if f.endswith('txt'):
                end_path = os.path.join(tra_dir, f)
                shutil.copy(start_path, end_path)
            else:
                # Copy to seg_dir and modify name
                end_path = os.path.join(seg_dir, f'man_seg{f[1:]}')
                shutil.copy(start_path, end_path)

                # Copy to tra dir and modify name
                end_path = os.path.join(tra_dir, f'man_track{f[1:]}')
                shutil.copy(start_path, end_path)

# Copy over results
for target, start_dirs in zip([ctc_gt, ctc_dc], [export_gt_dir, export_dc_dir]):
    for d in os.listdir(start_dirs):
        start_dir = os.path.join(start_dirs, d)
        end_dir = os.path.join(target, d)
        shutil.copytree(start_dir, end_dir)

In [18]:
benchmarks = []

for results_dir, s in zip([ctc_gt, ctc_dc], ['GT', 'Deepcell']):
    for data_id in data_ids:
        print(data_id)
        results = {
            'model': f'Baxter - {s}',
            'data_id': data_id
        }
        gt_dir = os.path.join(results_dir, f'{data_id}_GT/TRA')
        res_dir = os.path.join(results_dir, f'{data_id}_RES')

        # Deepcell benchmarking
        m = TrackingMetrics.from_isbi_dirs(gt_dir, res_dir, threshold=node_match_threshold)
        results.update(m.stats)

        # CTC metrics
        for metric, path in [('DET', 'DETMeasure'), ('SEG', 'SEGMeasure'), ('TRA', 'TRAMeasure')]:
            p = subprocess.run([os.path.join(ctc_software, operating_system, path), results_dir, data_id, num_digits],
                               stdout=subprocess.PIPE)
            outstring = p.stdout

            try:
                val = float(outstring.decode('utf-8').split()[-1])
                results[metric] = val
            except:
                print('Benchmarking failure', path, results_dir, data_id)
                print(outstring.decode('utf-8'))

        benchmarks.append(results)

df = pd.DataFrame(benchmarks)
df.to_csv('benchmarks.csv')

012
missed node 6_17 division completely
missed node 15_17 division completely
missed node 19_20 division completely
22_5 out degree = 2, daughters mismatch, gt and res degree equal.
missed node 29_17 division completely
missed node 59_10 division completely
missed node 60_34 division completely
76_7 out degree = 2, daughters mismatch, gt and res degree equal.
missed node 79_9 division completely
missed node 80_9 division completely
missed node 82_17 division completely
missed node 83_18 division completely
corrected division 79_9 as a frameshift division not an error
corrected division 82_17 as a frameshift division not an error
007
missed node 10_13 division completely
missed node 11_68 division completely
missed node 27_14 division completely
missed node 49_41 division completely
missed node 50_40 division completely
missed node 57_10 division completely
missed node 58_36 division completely
missed node 60_0 division completely
corrected division 10_13 as a frameshift division not a

In [19]:
df

model data_id  correct_division  mismatch_division  \
0         Baxter - GT     012                 6                  2   
1         Baxter - GT     007                13                  0   
2         Baxter - GT     009                 0                  0   
3         Baxter - GT     008                 0                  0   
4         Baxter - GT     001                33                  1   
5         Baxter - GT     006                 2                  0   
6         Baxter - GT     011                31                  3   
7         Baxter - GT     010                10                  0   
8         Baxter - GT     003                 2                  0   
9         Baxter - GT     004                 1                  0   
10        Baxter - GT     005                 5                  0   
11        Baxter - GT     002                 1                  0   
12  Baxter - Deepcell     012                 5                  1   
13  Baxter - Deepcell     007                12                  0   
14  Baxter - Deepcell     009                 0                  0   
15  Baxter - Deepcell     008                 0                  0   
16  Baxter - Deepcell     001                30                  2   
17  Baxter - Deepcell     006                 2                  0   
18  Baxter - Deepcell     011                20                  1   
19  Baxter - Deepcell     010                 8                  0   
20  Baxter - Deepcell     003                 1                  0   
21  Baxter - Deepcell     004                 1                  0   
22  Baxter - Deepcell     005                 5                  0   
23  Baxter - Deepcell     002                 1                  0   

    false_positive_division  false_negative_division  total_divisions  aa_tp  \
0                         0                        8               16   9788   
1                         0                        7               20   4943   
2                         0                        1                1    199   
3                         0                        0                0    383   
4                         9                       23               57  14656   
5                         0                        0                2    690   
6                         2                       20               54   9045   
7                         0                        5               15   3831   
8                         0                        1                3    997   
9                         0                        0                1    521   
10                        2                        3                8   2043   
11                        0                        0                1   1075   
12                        2                       10               16   9694   
13                        1                        8               20   4868   
14                        0                        1                1    199   
15                        0                        0                0    383   
16                       10                       25               57  14556   
17                        0                        0                2    690   
18                       14                       33               54   8767   
19                        1                        7               15   3720   
20                        0                        2                3    992   
21                        1                        0                1    502   
22                        2                        3                8   2012   
23                        0                        0                1   1069   

    aa_total  te_tp  te_total       DET       SEG       TRA  
0       9796  10064     10097  0.991186  0.989493  0.989699  
1       4945   5053      5056  0.996064  0.993224  0.994538  
2        199    204       206  0.997573  0.995124  0.996612  
3        383    